## Рефакторинг исходной таблицы

В этой тетрадке мы немножко играем с данными андийских языков.

Данные взяты [отсюда](https://docs.google.com/spreadsheets/d/1wLwgyR_YBa5yuKg8ozN4aLbi4wvRCEYkwX1Xhnryuuw/edit#gid=0). (Предоставлены проектом *Field NLP - morpology*) 

Наша задача распарсить данные и преобразовать их в онтологию. Нужно преобразовать словарные вхождения из таблицы в формат RDF и модель Ontolex lemon. 

На питон существует rdf либа:

In [5]:
# !pip install rdflib

Defaulting to user installation because normal site-packages is not writeable
  Using cached rdflib-5.0.0-py3-none-any.whl (231 kB)
  Using cached isodate-0.6.0-py2.py3-none-any.whl (45 kB)


  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.


RDF состоит из триплов, триплы это субъект-предикат-объект. Типа что - как_связано - с_чем. В либе rdflib вся эта сложная структура переведена в pythonic way -- у нас собирается что-то вроде контейнера\списка с 3-х элементными кортежами внутри. 

Вот пример из [документации](https://rdflib.readthedocs.io/en/stable/gettingstarted.html):

```
[
    (subject0, predicate0, object0),
    (subject1, predicate1, object1),
    ...
    (subjectN, predicateN, objectN)
 ]
```

Чтобы сразу не бросаться в огонь, я просто переведу саму таблицу с андийскими данными в pandas. А уже потом этот dataframe можно будет аккуратно переводить в rdf.

С гугл таблицами мне помог вот этот [туториал](https://medium.com/analytics-vidhya/how-to-read-and-write-data-to-google-spreadsheet-using-python-ebf54d51a72c)

Но к сожалению, это работает везде кроме колаба. Видимо, колаб не умеет поднимать локальные сервера.

In [76]:
import re
import pandas as pd
from googleapiclient.discovery import build
from google_auth_oauthlib.flow import InstalledAppFlow,Flow
from google.auth.transport.requests import Request
import os
import pickle
from tqdm import tqdm

In [2]:
andi_sheet_id = "1wLwgyR_YBa5yuKg8ozN4aLbi4wvRCEYkwX1Xhnryuuw"

SCOPES = ['https://www.googleapis.com/auth/spreadsheets.readonly']

# here enter the id of your google sheet
SAMPLE_SPREADSHEET_ID_input = andi_sheet_id
SAMPLE_RANGE_NAME = 'A1:S68794'

def main():
    global values_input, service
    creds = None
    if os.path.exists('token.pickle'):
        with open('token.pickle', 'rb') as token:
            creds = pickle.load(token)
    if not creds or not creds.valid:
        if creds and creds.expired and creds.refresh_token:
            creds.refresh(Request())
        else:
            flow = InstalledAppFlow.from_client_secrets_file(
                'client_secret.json', SCOPES)  # here enter the name of your downloaded JSON file
            creds = flow.run_local_server(port=0)
        with open('token.pickle', 'wb') as token:
            pickle.dump(creds, token)

    service = build('sheets', 'v4', credentials=creds)

    # Call the Sheets API
    sheet = service.spreadsheets()
    result_input = sheet.values().get(spreadsheetId=SAMPLE_SPREADSHEET_ID_input,
                                range=SAMPLE_RANGE_NAME).execute()
    values_input = result_input.get('values', [])

    if not values_input:
        print('No data found.')

main()

df = pd.DataFrame(values_input[1:], columns=values_input[0])

In [3]:
df.head()

id_word id_meaning id           lemma  ipa   morphology bor  \
0  ghod1238       1          1  1         АБÁДАЛIИ                        
1                 1          2  2         АБÁДАЛIИ                        
2                 2          1  3  АБÁДИЛ-АБÁДАЛIИ                        
3                 3          1  4       АБАЗИ́НА/В           (-щуб)   1   
4                 4          1  5       АБАЗИ́НА/Й      (-лълъилIи)   1   

      annotator   pos concepticon    meaning_ru  \
0  George Moroz   adv        1656       никогда   
1  George Moroz   adv                 ни за что   
2  George Moroz   adv              см. АБÁДАЛIИ   
3  George Moroz  noun                  абазинец   
4  George Moroz  noun                  абазинец   

                                          definition glottocode     reference  \
0  нареч. 1) никогда; абадалIи йаиччи ден биттиха...   ghod1238  Saidova 2006   
1  нареч. 1) никогда; абадалIи йаиччи ден биттиха...   ghod1238  Saidova 2006   
2                                то же, что абáдалIи   ghod1238  Saidova 2006   
3                                  I (-щуб) абазинец   ghod1238  Saidova 2006   
4                            II (-лълъилIи) абазинка   ghod1238  Saidova 2006   

  comments borrowing_source_word borrowing_source_comment 45,42%  
0                                                           3049  
1                                                           7932  
2                                                          10351  
3                                                           1391  
4                                                           4124

Делаем кокой-то RDF (пока не знаем какой, просто делаем, чтобы знать, что мы такое умеем)

In [6]:
import rdflib
from rdflib.namespace import RDF, RDFS, OWL, DC, DCTERMS
from rdflib.term import URIRef, Literal

In [102]:
g = rdflib.Graph(identifier='http://example.org/ontolex/andi#')  # пока рандомная ссылка

In [103]:
andi = rdflib.Namespace('http://example.org/ontolex/andi#')  # Корневой Namespace с рандомной ссылкой

ontolex = rdflib.Namespace('http://www.w3.org/ns/lemon/ontolex#')  # основная модель
lexinfo = rdflib.Namespace('http://www.lexinfo.net/ontology/2.0/lexinfo#')  # обозначение морфологических тегов
lime = rdflib.Namespace('http://www.w3.org/ns/lemon/lime#')
#synsem = rdflib.Namespace('http://www.w3.org/ns/lemon/synsem#')  # синтаксис
#decomp = rdflib.Namespace('http://www.w3.org/ns/lemon/decomp#')  # синтаксис
vartrans = rdflib.Namespace('http://www.w3.org/ns/lemon/vartrans#')  # для обозначения переводов и вариантов слов
skos = rdflib.Namespace('http://www.w3.org/2004/02/skos#')

In [104]:
g.bind('ontolex', ontolex)
g.bind('lexinfo', lexinfo)
g.bind('dct', DCTERMS)  # Это для того, чтобы названия ISO языков грузились
g.bind('rdfs', RDFS)
g.bind('lime', lime)  # ??
#g.bind('synsem', synsem)
#g.bind('decomp', decomp)
g.bind('vartrans', vartrans)
g.bind('skos', skos)

lexicon_andi = URIRef(andi)

In [105]:
# Надо вот тут добавить все типы триплов, чтобы они добавились в префиксы ниже
g.set((lexicon_andi, RDF.type, lime.Lexicon))
g.set((lexicon_andi, ontolex.language, Literal("ru, ani")))
g.set((lexicon_andi, RDFS.comment, Literal("lexicon-information_name:Andi-Russian", lang="en")))

#lime:Lexicon_Kadag1884_bbl a ontolex:Lexicon.
#lime:Lexicon_Kadag1884_bbl ontolex:language "bbl", "ka", "ru".
#lime:Lexicon_Kadag1884_bbl rdfs:comment "lexicon-information_name:Kadagidze - Batsbi-Georgian-Russian"@en.

#g.set((apics_doc, ligt.hasUtterances, apics.examples))
#g.set((apics.examples, RDF.type, ligt.InterlinearCollection))
#Probably it should also be a `dc:bibliographicCitation`
#g.set((apics.examples, RDFS.comment, Literal(apics_dataset.properties['dc:bibliographicCitation '], lang="en")))

In [106]:
# сделала пустой turtle, прикольно
print(g.serialize(format='turtle').decode('utf-8'))

@prefix lime: <http://www.w3.org/ns/lemon/lime#> .
@prefix ontolex: <http://www.w3.org/ns/lemon/ontolex#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .

<http://example.org/ontolex/andi#> a lime:Lexicon ;
    rdfs:comment "lexicon-information_name:Andi-Russian"@en ;
    ontolex:language "ru, ani" .




In [107]:
# check what POS names are used in the original table
df['pos'].value_counts().index.tolist()

['',
 'noun',
 'verb',
 'adj',
 'noun III',
 'adv',
 'noun IV',
 'masdar',
 'noun V',
 'num',
 'intj',
 'part',
 'noun I',
 'particle',
 '?',
 'noun I,II',
 'noun II',
 'excl',
 'pron',
 'expression',
 'post',
 'verb ',
 'participle',
 'masd',
 'conj',
 'onomatope',
 'adverb',
 'adv?',
 'prep',
 'noun?',
 'verb/adj',
 'noun II,IV',
 'adp',
 'morph',
 'part?',
 'adj?',
 'adposition',
 'noun I,II,III',
 'x',
 'particle?',
 'masdar ',
 'noun ',
 'ordinal',
 'ayx',
 'pred',
 'verb?',
 'pronoun',
 'verb/adv',
 'expr',
 ' adv',
 'part, adv',
 'expression/noun',
 'noun VI',
 'adposition?',
 'adv ',
 'noun I,I',
 'morpheme',
 '???',
 'noun I,III',
 'num?',
 '? :)',
 'masdar?',
 'excl?',
 'adj ',
 'gerund?',
 ' verb']

In [108]:
for lemma in tqdm(df['lemma '][1:10000]):
    if ' ' in lemma:
        lemma = lemma.replace(' ', '_')
        
    g.add((Literal(lemma), RDF.type, ontolex.LexicalEntry))
    g.add((Literal(lemma), ontolex.canonicalForm, Literal(lemma + '_form')))
    g.add((Literal(lemma + '_form'), ontolex.writtenRep, Literal(lemma, lang='ani')))
    g.add((Literal(lemma), DCTERMS.language, URIRef('http://id.loc.gov/vocabulary/iso639-3/ani')))
    #g.add((Literal(lemma), ontolex.sense, Literal(lemma + '_sense')))
    
    # у некоторых слов есть несколько переводов, это обозначено, как новые строки таблицы
    # пока чтобы не париться я беру только один перевод
    translation = df[df['lemma '] == lemma]['meaning_ru']
    if not translation.empty:
        translation = translation.values[0]
        if ' ' in translation:
            translation = translation.replace(' ', '_')
            
        g.add((Literal(lemma), vartrans.Translation, Literal(translation)))
        g.add((Literal(translation), vartrans.Translation, Literal(lemma)))

        g.add((Literal(translation), RDF.type, ontolex.LexicalEntry))
        g.add((Literal(translation), ontolex.LexicalForm, Literal(translation + '_form')))
        g.add((Literal(translation + '_form'), ontolex.writtenRep, Literal(translation, lang='rus')))
        g.add((Literal(translation), DCTERMS.language, URIRef('http://id.loc.gov/vocabulary/iso639-2/rus')))
        #g.add((Literal(translation), ontolex.sense, Literal(translation + '_sense')))
        
        definition = df[df['lemma '] == lemma]['definition']
        if not definition.empty:
            definition = definition.values[0]
            if definition != '':
                g.add((Literal(translation + '_lexical_concept'), RDF.type, ontolex.LexicalConcept))
                g.add((Literal(translation + '_lexical_concept'), skos.definition, Literal(definition)))
                g.add((Literal(translation + '_lexical_concept'), ontolex.isEvokedBy, Literal(lemma)))
                g.add((Literal(lemma), ontolex.evokes, Literal(translation + '_lexical_concept')))
    
    ipa = df[df['lemma '] == lemma]['ipa']
    if not ipa.empty:
        ipa = ipa.values[0]
        if ipa != '':
            g.add((Literal(lemma + '_form'), ontolex.phoneticRep, Literal(ipa, lang='ipa')))
        
    morph = df[df['lemma '] == lemma]['morphology']
    if not morph.empty:
        morph = morph.values[0]
        if morph != '':
            g.add((Literal(lemma), ontolex.morphologicalPattern, Literal(morph)))
        
    pos = df[df['lemma '] == lemma]['pos']
    if not pos.empty:
        pos = pos.values[0]
        if pos != '':
            if re.match(r'.*?[nN]oun.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.noun))
            if re.match(r' ?adj.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.adjective))
            if re.match(r'.*?adv.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.adverb))
            if re.match(r' ?verb.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.verb))
            if re.match(r'num.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.numeral))
            if re.match(r'.*?ord.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.indefiniteOrdinalNumeral))
            if re.match(r' ?adp.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.adposition))
            if re.match(r' ?gerund.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.gerundive))
            if re.match(r'.*?participle.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.participle))
            if re.match(r'.*?part.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.particle))
            if re.match(r'excl.*', pos):
                g.add((Literal(lemma), lexinfo.partOfSpeech, lexinfo.exclamativePoint))


100%|██████████████████████████████████████████████████████████████████████████████| 9999/9999 [10:05<00:00, 17.01it/s]


In [109]:
print(g.serialize(format='turtle').decode('utf-8'))

@prefix dct: <http://purl.org/dc/terms/> .
@prefix lexinfo: <http://www.lexinfo.net/ontology/2.0/lexinfo#> .
@prefix lime: <http://www.w3.org/ns/lemon/lime#> .
@prefix ontolex: <http://www.w3.org/ns/lemon/ontolex#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix skos: <http://www.w3.org/2004/02/skos#> .
@prefix vartrans: <http://www.w3.org/ns/lemon/vartrans#> .

<http://example.org/ontolex/andi#> a lime:Lexicon ;
    rdfs:comment "lexicon-information_name:Andi-Russian"@en ;
    ontolex:language "ru, ani" .

"-ВÁРАЛА_//_ВĀЛЛА" a ontolex:LexicalEntry ;
    dct:language <http://id.loc.gov/vocabulary/iso639-3/ani> ;
    ontolex:canonicalForm "-ВÁРАЛА_//_ВĀЛЛА_form" .

"-ВŌХО_//_-ŌХО" a ontolex:LexicalEntry ;
    dct:language <http://id.loc.gov/vocabulary/iso639-3/ani> ;
    ontolex:canonicalForm "-ВŌХО_//_-ŌХО_form" .

"-ВУ_//_-ВӮᴴ" a ontolex:LexicalEntry ;
    dct:language <http://id.loc.gov/vocabulary/iso639-3/ani> ;
    ontolex:canonicalForm "-ВУ_//_-ВӮᴴ_form" .

"-В

In [110]:
g.serialize(destination='output.ttl', format='turtle')